In [1]:
from transformers import BertTokenizer, BertForSequenceClassification, Trainer, TrainingArguments
from transformers import DebertaV2Tokenizer, DebertaV2ForSequenceClassification
import torch
from sklearn.model_selection import train_test_split
import numpy as np
from sklearn.metrics import accuracy_score, f1_score
import pandas as pd
import random
from sklearn.utils import shuffle


# load dataset

In [2]:
# df = pd.read_csv('../FINAL_GEMINI_CHATGPT_DEFAULT_fixed_20250529_185815.csv')
df = pd.read_csv('../FINAL_GEMINI_CHATGPT_FULL_fixed_20250529_185657.csv')
print(len(df))

50000


In [5]:
# only when you train default vs advers
# test_df = pd.read_csv('../FINAL_GEMINI_CHATGPT_ADVERS_fixed_20250529_185904.csv')
# print(len(test_df))

10000


# train model

#### --- 1. Data Preparation ---

In [3]:
df_clean = df.dropna(subset=['generated']).copy() 

# Ensure 'chapter' and 'generated' are strings
df_clean['chapter'] = df_clean['chapter'].astype(str)
df_clean['generated'] = df_clean['generated'].astype(str)

In [6]:
test_size = 0.2

unique_ids = set(df_clean['document_id'])

print(f'Unique docs:{len(unique_ids)}')

num_docs = int(len(unique_ids) * 0.2)

unique_ids_list = list(unique_ids)
np.random.seed(24)
np.random.shuffle(unique_ids_list)

test_ids = unique_ids_list[:num_docs]

# Create test set by filtering documents with selected IDs
val_df = df_clean[df_clean['document_id'].isin(test_ids)].copy()

# Create training set with remaining documents
train_df = df_clean[~df_clean['document_id'].isin(test_ids)].copy()

print(f"Test set size: {len(val_df)}")
print(f"Training set size: {len(train_df)}")

Unique docs:3254
Test set size: 10123
Training set size: 39877


In [7]:
# Create lists of texts and corresponding labels
train_texts = train_df['chapter'].tolist() + train_df['generated'].tolist()
train_labels = [0] * len(train_df) + [1] * len(train_df)

val_texts = val_df['chapter'].tolist() + val_df['generated'].tolist()
val_labels = [0] * len(val_df) + [1] * len(val_df)

In [3]:
#### old way
# Create lists of texts and corresponding labels
# Label 0 for original, 1 for AI-generated
texts = df_clean['chapter'].tolist() + df_clean['generated'].tolist()
labels = [0] * len(df_clean) + [1] * len(df_clean)

# Split data into training and validation sets
train_texts, val_texts, train_labels, val_labels = train_test_split(
    texts, labels, test_size=0.2, random_state=42, stratify=labels
)


In [8]:
print(len(train_texts)),
print(len(val_texts))
print(sum(len(text.split()) for text in train_texts) / len(train_texts))
print(sum(len(text.split()) for text in val_texts) / len(val_texts))

79754
20246
467.88586152418685
470.1667489874543


#### --- 2. Load Tokenizer and Model ---

In [9]:
from transformers import DebertaV2Tokenizer, DebertaV2ForSequenceClassification, AutoTokenizer, AutoModelForSequenceClassification

# Use a Romanian BERT model
model_name = "dumitrescustefan/bert-base-romanian-cased-v1"
tokenizer = BertTokenizer.from_pretrained(model_name)
model = BertForSequenceClassification.from_pretrained(model_name, num_labels=2) # 2 labels: original vs generated


# model_name = "xlm-roberta-base"
# tokenizer = AutoTokenizer.from_pretrained(model_name)
# model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=2)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at dumitrescustefan/bert-base-romanian-cased-v1 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


#### --- 3. Tokenize Data ---

In [10]:
# Tokenize the texts
train_encodings = tokenizer(train_texts, truncation=True, padding=True, max_length=128)
val_encodings = tokenizer(val_texts, truncation=True, padding=True, max_length=128)

In [11]:
class TextDataset(torch.utils.data.Dataset):
    def __init__(self, encodings, labels):
        self.encodings = encodings
        self.labels = labels

    def __getitem__(self, idx):
        # Ensure all encoding keys are converted to tensors
        item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()}
        item['labels'] = torch.tensor(self.labels[idx])
        return item

    def __len__(self):
        # Use the length of one of the encoding lists (e.g., 'input_ids')
        return len(self.encodings['input_ids'])

In [12]:
train_dataset = TextDataset(train_encodings, train_labels)
val_dataset = TextDataset(val_encodings, val_labels)

#### --- 5. Set up Trainer ---

In [13]:
training_args = TrainingArguments(
    output_dir='./results_romanian_bert_128_full_fixed',          # Output directory for checkpoints and logs
    num_train_epochs=1,              # Reduce epochs for a quicker example run
    per_device_train_batch_size=8,   # Adjust based on GPU memory
    per_device_eval_batch_size=16,  # Adjust based on GPU memory
    warmup_steps=100,                # Number of warmup steps for learning rate scheduler
    weight_decay=0.01,               # Strength of weight decay
    logging_dir='./logs',            # Directory for storing logs
    logging_steps=50,               # Log metrics every 50 steps
    eval_strategy="steps",           # Evaluate during training
    eval_steps=500,                  # Evaluate every 500 steps
    save_strategy="steps",           # Save checkpoint strategy
    save_total_limit=2,             # Limit the total amount of checkpoints
    save_steps=1000,                  # Save checkpoint every 500 steps
    load_best_model_at_end=True,     # Load the best model found during training
    metric_for_best_model="accuracy", # Use accuracy to determine the best model
    greater_is_better=True,
    fp16=torch.cuda.is_available(),  # Use mixed precision if CUDA is available
    report_to="none"                   # Disable reporting to wandb/tensorboard for this example
)

# Define evaluation metric (accuracy)

def compute_metrics(pred):
    labels = pred.label_ids
    preds = pred.predictions.argmax(-1)
    acc = accuracy_score(labels, preds)
    f1 = f1_score(labels, preds)
    false_positive_rate = np.sum((preds == 1) & (labels == 0)) / np.sum(labels == 0)
    false_negative_rate = np.sum((preds == 0) & (labels == 1)) / np.sum(labels == 1)
    return {
        'accuracy': acc,
        'f1': f1,
        'false_positive_rate': false_positive_rate,
        'false_negative_rate': false_negative_rate
    }

In [ ]:

# Initialize Trainer
trainer = Trainer(
    model=model,                         # The instantiated Transformers model to be trained
    args=training_args,                  # Training arguments, defined above
    train_dataset=train_dataset,         # Training dataset
    eval_dataset=val_dataset,            # Evaluation dataset
    compute_metrics=compute_metrics      # Function to compute metrics
)

# --- 6. Train the Model ---
print("Starting training...")
trainer.train()

print("Training finished.")

# --- 7. Evaluate the Model ---
print("Evaluating model...")
eval_results = trainer.evaluate()
print(f"Evaluation results: {eval_results}")

Starting training...


#### --- Optional: Save the fine-tuned model and tokenizer ---Please check name--

In [15]:
save_path = "./fine_tuned_romanian_bert_128_full2"

# Save model and tokenizer, overwriting if it already exists
print(f"Saving/Updating model and tokenizer to {save_path}...")
model.save_pretrained(save_path)
tokenizer.save_pretrained(save_path)
print(f"Model and tokenizer saved to {save_path}")


Saving/Updating model and tokenizer to ./fine_tuned_romanian_bert_128_full2...
Model and tokenizer saved to ./fine_tuned_romanian_bert_128_full2


#### plots

In [16]:
# Save training history to a file
import json
import os

# Create directory for training history if it doesn't exist
history_dir = "./training_history_romanian_bert_128_full"
os.makedirs(history_dir, exist_ok=True)

# Get training history from trainer
history = trainer.state.log_history

# Save to JSON file with timestamp
from datetime import datetime
timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
history_file = os.path.join(history_dir, f"training_history_{timestamp}.json")

with open(history_file, 'w') as f:
    json.dump(history, f, indent=2)

print(f"Training history saved to {history_file}")

# Optional: Save a summary of key metrics
metrics_summary = {
    'final_accuracy': eval_results['eval_accuracy'],
    'final_f1': eval_results['eval_f1'],
    'final_false_positive_rate': eval_results['eval_false_positive_rate'],
    'final_false_negative_rate': eval_results['eval_false_negative_rate']
}

summary_file = os.path.join(history_dir, f"metrics_summary_{timestamp}.json")
with open(summary_file, 'w') as f:
    json.dump(metrics_summary, f, indent=2)

print(f"Metrics summary saved to {summary_file}")

Training history saved to ./training_history_romanian_bert_128_full/training_history_20250530_153926.json
Metrics summary saved to ./training_history_romanian_bert_128_full/metrics_summary_20250530_153926.json


In [ ]:

# Plot training history
import matplotlib.pyplot as plt
import seaborn as sns

# Set style
plt.style.use('seaborn-v0_8')  # Use the correct style name
sns.set_palette("husl")

# Create figure with subplots
fig, (ax1, ax2) = plt.subplots(2, 1, figsize=(12, 10))
fig.suptitle('Training History', fontsize=16)

# Plot loss - handle missing 'loss' key by using eval_loss instead
ax1.plot([x['step'] for x in history], [x.get('loss', x.get('eval_loss', 0)) for x in history], label='Training Loss')
ax1.set_xlabel('Steps')
ax1.set_ylabel('Loss')
ax1.set_title('Training Loss Over Time')
ax1.legend()
ax1.grid(True)

# Plot learning rate - handle missing 'learning_rate' key
ax2.plot([x['step'] for x in history], [x.get('learning_rate', 0) for x in history], label='Learning Rate', color='orange')
ax2.set_xlabel('Steps')
ax2.set_ylabel('Learning Rate')
ax2.set_title('Learning Rate Schedule')
ax2.legend()
ax2.grid(True)

# Adjust layout and display
plt.tight_layout()
plt.show()

# Print final metrics
print("\nFinal Metrics:")
print(f"Accuracy: {metrics_summary['final_accuracy']:.4f}")
print(f"F1 Score: {metrics_summary['final_f1']:.4f}")
print(f"False Positive Rate: {metrics_summary['final_false_positive_rate']:.4f}")
print(f"False Negative Rate: {metrics_summary['final_false_negative_rate']:.4f}")


# extra eval checks

In [52]:
def get_validation_from_original(filename):
    df = pd.read_csv(filename)
    val_texts = df['sample'].tolist()
    val_labels = [0] * len(df)
    return val_texts, val_labels

def get_validation_data(filename):
    df = pd.read_csv(filename)

    val_texts = df['chapter'].tolist() + df['generated'].tolist()
    val_labels = [0] * len(df) + [1] * len(df)
    
    #shuffle the data
    indices = np.arange(len(val_texts))
    np.random.shuffle(indices)
    val_texts = [val_texts[i] for i in indices]
    val_labels = [val_labels[i] for i in indices]
    
    return val_texts, val_labels

# extra_val_file = '../FINAL_GEMINI_CHATGPT_fixed.csv'
# extra_val_file = '../generation/gemini/non_ai_doctorat_FINAL_GEMINI_23900_24400_final_20250520_212903.csv'
# extra_val_texts, extra_val_labels = get_validation_data(extra_val_file)

extra_val_original_file = '../dataframe_2800-5600_ch_marker_chapters_mds_marker_0_500_clean.csv'
extra_val_texts, extra_val_labels = get_validation_from_original(extra_val_original_file)

In [ ]:
# If you want to use the same validation data, uncomment the following lines
# extra_val_texts = val_texts
# extra_val_labels = val_labels

In [53]:
def get_model_and_tokenizer(saved_model_path):
    if (saved_model_path == None):
        print("Using default model and tokenizer")
        return model, tokenizer
        
    print(f"Loading model and tokenizer from {saved_model_path}...")
    loaded_tokenizer = BertTokenizer.from_pretrained(saved_model_path)
    loaded_model = BertForSequenceClassification.from_pretrained(saved_model_path)
    return loaded_model, loaded_tokenizer

# saved_model_path = "./fine_tuned_RoBERT_128_base_detector"
loaded_model, loaded_tokenizer = get_model_and_tokenizer(None)


Using default model and tokenizer


In [54]:
print("Tokenizing validation data...")
val_encodings_loaded = loaded_tokenizer(extra_val_texts, truncation=True, padding=True, max_length=128)

# Re-create the validation dataset
val_dataset_loaded = TextDataset(val_encodings_loaded, extra_val_labels)
print("Validation dataset created.")


eval_trainer = Trainer(
    model=loaded_model,
    args=training_args,  # Reusing args 
    eval_dataset=val_dataset_loaded,
    compute_metrics=compute_metrics # Reusing compute_metrics 
)

# Evaluate the loaded model on the validation set
print("Evaluating the loaded model...")
evaluation_results = eval_trainer.evaluate()

# Print the evaluation results
print("\n--- Evaluation Results ---")
print(f"Validation Accuracy: {evaluation_results.get('eval_accuracy', 'N/A'):.4f}")
print(f"Validation Loss: {evaluation_results.get('eval_loss', 'N/A'):.4f}")
print(f"Full evaluation metrics: {evaluation_results}")

Tokenizing validation data...
Validation dataset created.
Evaluating the loaded model...



--- Evaluation Results ---
Validation Accuracy: 0.7068
Validation Loss: 1.7244
Full evaluation metrics: {'eval_loss': 1.7244079113006592, 'eval_model_preparation_time': 0.0038, 'eval_accuracy': 0.7067802626908058, 'eval_false_positive_rate': 0.29321973730919415, 'eval_false_negative_rate': nan, 'eval_runtime': 24.2219, 'eval_samples_per_second': 232.6, 'eval_steps_per_second': 14.574}


/tmp/ipykernel_13603/2672737994.py:31: RuntimeWarning: invalid value encountered in scalar divide
  false_negative_rate = np.sum((preds == 0) & (labels == 1)) / np.sum(labels == 1)


#### --- 8. Analyze wrong predictions ---

In [ ]:
def evaluate_and_print_wrongs(texts, true_labels, model, tokenizer, num_examples=None):
    # Move model to appropriate device
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    model.to(device)
    model.eval()  # Set model to evaluation mode
    
    wrong_predictions = []
    
    # If num_examples is not specified, use all examples
    if num_examples is None:
        num_examples = len(texts)
    else:
        num_examples = min(num_examples, len(texts))
    
    for i in range(num_examples):
        text = texts[i]
        true_label = true_labels[i]
        
        # Tokenize and prepare input
        inputs = tokenizer(text, return_tensors="pt", truncation=True, padding=True, max_length=512)
        inputs = {k: v.to(device) for k, v in inputs.items()}
        
        # Get prediction
        with torch.no_grad():
            outputs = model(**inputs)
            logits = outputs.logits
            probabilities = torch.softmax(logits, dim=1).squeeze().tolist()
            predicted_class_id = torch.argmax(logits, dim=1).item()
        
        # If prediction is wrong, store the example
        if predicted_class_id != true_label:
            wrong_predictions.append({
                'index': i,
                'text': text,
                'true_label': 'AI-generated' if true_label == 1 else 'Original',
                'predicted_label': 'AI-generated' if predicted_class_id == 1 else 'Original',
                'confidence': max(probabilities)
            })
    
    # Print summary
    print(f"Total examples evaluated: {num_examples}")
    print(f"Number of wrong predictions: {len(wrong_predictions)}")
    print(f"Accuracy: {(num_examples - len(wrong_predictions)) / num_examples:.2%}")
    print("\nWrong Predictions:")
    print("-" * 80)
    
    for pred in wrong_predictions:
        print(f"\nIndex: {pred['index']}")
        print(f"Text: {pred['text']}")
        print(f"True label: {pred['true_label']}")
        print(f"Predicted label: {pred['predicted_label']}")
        print(f"Confidence: {pred['confidence']:.2%}")
        print("-" * 80)

# Run the evaluation
evaluate_and_print_wrongs(extra_val_texts, extra_val_labels, loaded_model, loaded_tokenizer)

Total examples evaluated: 5634
Number of wrong predictions: 1862
Accuracy: 66.95%

Wrong Predictions:
--------------------------------------------------------------------------------

Index: 21
Text: Sindromul carcinoid implică peste patruzeci de substanțe, în schimb, rolul fiecăreia în apariția simptomatologiei și complicațiilor rămâne incert, Serotonina pare a fi markerul primordial asociat cu sindromul carcinoid, la fel ca și histamina, kalikreina, prostaglandine și tahikinine. Substanțele vasoactive secretate de obicei de către tumorile funcționale (serotonina, substanța P, histamine, catecolamine) nu sunt inactivate la nivel hepatocitar, producând flush facial caracteristic. Mecanismul bronhospasmului se bazează pe eliberarea de histamină si acid 5- hidroxi-indolacetic, metabolitul serotoninei.

 Fiziopatologia bolii cardiace carcinoide rămâne incertă, deși se cunoaște rolul serotoninei în stimularea creșterii fibroblastice, conducând la formarea de țesut fibros la nivelul valvelo

#### --- Single inference ---

In [66]:
# index = 5
# test_text = extra_val_texts[index]
# true_label = extra_val_labels[index]
test_text = '''Evaziunea onirică macedonskiană se materializează într-un „spațiu meridional, luminos, fierbinte, colorat, exotic”, printr-un zbor care oferă o viziune panoramică „cu străluciri de materii prețioase, cu parfumuri, roze, cântece, șoapte, cu freamăt de aripi”. Poetul, geniu damnat la mizerie în „Noapte de decembrie” (p. 163), evadează în Bagdad, unde, în calitate de emir, se simte „furat de-o visare” (simbol al absolutului); în „Noaptea de noiembrie” (p. 81), visul ia forma unui zbor spre Sud, spre Italia legendară a lui Alecsandri, Duiliu Zamfirescu sau, mai târziu, a lui Mateiu Caragiale. Visul este, așadar, un spațiu compensatoriu, dar această compensație este, la rândul ei, limitată, întrucât idealul nu poate fi atins nici măcar în vis. Emirul nu ajunge la cetatea visată, ci moare în fața acesteia, pentru a se împlini spiritual.

În „Thalassa”, motivul central al insulei oferă prilejul unei împliniri erotice (asemenea prozei eminesciene), într-un cadru cromatic și oniric luxuriant. Iubirea se află sub semnul lui Eros și al lui Priap, este „agresivă, frenetică, exclusiv carnală, dar tocmai de aceea incompletă” și se desfășoară într-un regim diurn, solar, cu o senzualitate incandescentă, totul fiind „forță, spasm, extaz, suferință” și tragism. Izvorul visului nu este, ca la romantici, livresque, ci predominant senzorial, instinctiv („el simțea că-i crește o inimă antică”), și doar tangențial cult (inspirat din scrierile lui Teocrit și Xenofon). Thalassa parcurge stări de la dorințe confuze exprimate prin vis-coșmar la extaz, delir și halucinație, printr-un somn letargic („Dogoreala stâncei ce înmagazinase o parte a căldurei amiazului începu să-l apese cu o abstragere de timp și de loc. Cu câte cinci simțurile istovite, cugetările i se nimiceau, și el se cufunda în nespus de înalt mulțumire a neființei” – p. 5), se simte atras de mare („Mărgăritare și topaze, safire și smaralde se deșirau de pe toate, iar mari crini albi înfloreau și pe o coastă a lor și pe cealaltă …. Prăpastia verzuie, în care Neptun și Amfitrita și-au clădit palatele de smarald, împingea deasupra valurilor o văpaie ușoară” – p. 10). Visul, în acest caz idealul, se va împlini în și prin mare, idealul la care visează de mic, după ce refuză o iubire epuizată și epuizantă cu Caliope. „Sfârșitul lui Thalassa, dăruit în fine mării, se consumă în transă, cu viziuni și senzații sublime. Sacrificiu, apoteoză, nuntă mitică, dar cu sens thanatic, sau toate laolaltă? Ambiguitatea potențează finalul prin deschidere spre mister”. Așadar, asemenea viziunii romanticilor, pentru care adevărata realitate nu există decât în vis, Thalassa își găsește împlinirea în visul absolut, întrucât „simbolismul vine dintr-un secol romantic și tocmai de aceea, presimte o anume presiune a realului, din care se va naște literatura angoasei moderne, literatura absurdului”.'''

true_label = 1 # 0 for original, 1 for AI-generated


print(f"True label: {'AI-generated' if true_label == 1 else 'Original'}")
print(f"Testing text: \n{test_text[:1000]}") 

inputs = loaded_tokenizer(test_text, return_tensors="pt", truncation=True, padding=True, max_length=512)

# Move inputs to the same device as the model if using GPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
loaded_model.to(device)
inputs = {k: v.to(device) for k, v in inputs.items()}

# Get prediction from the model
# No need to compute gradients for inference
with torch.no_grad():
    outputs = loaded_model(**inputs)
    logits = outputs.logits
    predicted_class_id = torch.argmax(logits, dim=1).item()

# Interpret the prediction
predicted_label = "AI-generated" if predicted_class_id == 1 else "Original"
print(f"Predicted label: {predicted_label}")

# Optional: Print probabilities
probabilities = torch.softmax(logits, dim=1).squeeze().tolist()
print(f"Probabilities: Original={probabilities[0]:.4f}, AI-generated={probabilities[1]:.4f}")


True label: AI-generated
Testing text: 
Evaziunea onirică macedonskiană se materializează într-un „spațiu meridional, luminos, fierbinte, colorat, exotic”, printr-un zbor care oferă o viziune panoramică „cu străluciri de materii prețioase, cu parfumuri, roze, cântece, șoapte, cu freamăt de aripi”. Poetul, geniu damnat la mizerie în „Noapte de decembrie” (p. 163), evadează în Bagdad, unde, în calitate de emir, se simte „furat de-o visare” (simbol al absolutului); în „Noaptea de noiembrie” (p. 81), visul ia forma unui zbor spre Sud, spre Italia legendară a lui Alecsandri, Duiliu Zamfirescu sau, mai târziu, a lui Mateiu Caragiale. Visul este, așadar, un spațiu compensatoriu, dar această compensație este, la rândul ei, limitată, întrucât idealul nu poate fi atins nici măcar în vis. Emirul nu ajunge la cetatea visată, ci moare în fața acesteia, pentru a se împlini spiritual.

În „Thalassa”, motivul central al insulei oferă prilejul unei împliniri erotice (asemenea prozei eminesciene), într-

# Features analysis
